In [ ]:
# ..... annotate cell clusters ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)
library(data.table)
library(dplyr)

In [3]:
# list of stages and samples
stages = rep(c('stage14', 'stage17', 'stage21'), each = 3)
samples = paste0('sample', c('4', '7', '8A', '3_Triangle', '5B', '5Y', '1A', '1B', '2'))

In [4]:
# load list of orthologs
om = read.delim('mouse_turtle_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'turtle', 'LCA', 'homology_type', 'orthology_confidence')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12741     5

mouse  turtle LCA        homology_type    orthology_confidence
11 mt-Nd2 ND2    Vertebrata ortholog_one2one 1

In [5]:
# function to get top 100 markers for each cell type
get_top_markers <- function(markers, ctypes){
    markers$rank = NA
    for(ii in 1:length(ctypes)){
        id = which(markers$cell_type==ctypes[ii])
        markers$rank[id] = 1:length(id)
    }
    return(markers)
}

In [11]:
# load class markers
markers = fread('~/septation/markers/Qiu/Qiu_major_celltype_markers_E9.5.csv.gz')
markers$gene <- om$turtle[match(markers$gene, om$mouse)]
markers <- markers[!is.na(markers$gene),]
ctypes = unique(markers$cell_type)

# subclass markers stratified by class
markers2 = fread('~/septation/markers/Qiu/Qiu_minor_celltype_markers_E9.5.csv.gz')
markers2$gene <- om$turtle[match(markers2$gene, om$mouse)]
markers2 <- markers2[!is.na(markers2$gene),]
ctypes2 = unique(markers2$cell_type)

# get rank of markers
markers = get_top_markers(markers, ctypes)
markers2 = get_top_markers(markers2, ctypes2)

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=100),c('group', 'cell_type', 'gene')])
top_markers2 = as_tibble(markers2[which(markers2$rank<=100),c('group', 'cell_type', 'gene')])

top_markers[1:2,]
top_markers2[1:2,]

group cell_type      gene  
1 all   Cardiomyocytes RYR2  
2 all   Cardiomyocytes SLC8A1

group       cell_type                  gene 
1 Endothelium Arterial endothelial cells MECOM
2 Endothelium Arterial endothelial cells VEGFC

In [59]:
unique(top_markers2$cell_type[top_markers2$group=='Mesoderm'])

[1] "Chondrocytes (Atp1a2+)"                 
 [2] "Chondrocytes (Otor+)"                   
 [3] "Dermatome"                              
 [4] "Dermomyotome"                           
 [5] "Early chondrocytes"                     
 [6] "Facial mesenchyme"                      
 [7] "Fibroblasts"                            
 [8] "Lateral plate and intermediate mesoderm"
 [9] "Limb mesenchyme progenitors"            
[10] "Mesodermal progenitors (Tbx6+)"         
[11] "Sclerotome"

In [12]:
# load data
pb = txtProgressBar(min = 0, max = length(samples), initial = 0)

for(sampleid in 1:3){
    file0 = paste0(stages[sampleid], '_', samples[sampleid], '_data.rds')
    sce = readRDS(file0)
    
    # get SCE object
    sc3 = SingleCellExperiment(list(counts = LayerData(sce, assay = 'RNA', layer = 'counts')))
    colData(sc3) <- DataFrame(sce@meta.data)
    assay(sc3, "cpm") = convert_to_cpm(assay(sc3))
    
        # predict cell type class
    ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
    ct_enrichment = compute_marker_enrichment(ct_scores)
    ct_pred = assign_cells(ct_scores)
    
    # ct_pred[1:3,]
    # table(ct_pred$predicted)
    
    # get cell subclass labels
    sub_scores = score_cells(log1p(cpm(sc3)), top_markers2)
    sub_enrichment = compute_marker_enrichment(sub_scores, by_group = TRUE)
    sub_pred = assign_cells(sub_scores, group_assignment = ct_pred$predicted)
    
    # sub_pred[1:3,]
    # table(sub_pred$predicted[sub_pred$group=='Mesoderm'])
    
    # <20 cells of a type - make assignment NA
    rm_ids = names(which(table(sub_pred$predicted)<20))
    sub_pred$predicted[which(sub_pred$predicted %in% rm_ids)] <- NA
    
    # make combined prediction df
    newdf = data.frame(barcode = rownames(ct_pred), class = ct_pred$predicted, celltype = sub_pred$predicted)
    newdf$final_celltype = newdf$celltype
    for(ii in 1:dim(newdf)[1]){
       if(is.na(newdf$celltype[ii])){
           newdf$final_celltype[ii] = newdf$class[ii]
       }
    }
    # newdf[1,]
    
    # save
    write.table(newdf, file = paste0('annotations/', stages[sampleid], '_', samples[sampleid], '_Qiu_celltypes.csv'),
                sep = ',', row.names = F, col.names = T, quote = F)
    
    setTxtProgressBar(pb, sampleid)
}

Warning message in assign_cells(sub_scores, group_assignment = ct_pred$predicted):
“Some group assignments (Primitive_erythroid, Definitive_erythroid, Megakaryocytes, Neural_crest_PNS_glia, unassigned) do not match groups in the score matrix (Cardiomyocytes, Endothelium, Epithelial_cells, Mesoderm, Muscle_cells, Neural_crest_PNS_neurons, White_blood_cells) and will result in NA predictions.”


Warning message in assign_cells(sub_scores, group_assignment = ct_pred$predicted):
“Some group assignments (Primitive_erythroid, Neural_crest_PNS_glia, Megakaryocytes, Definitive_erythroid, unassigned) do not match groups in the score matrix (Cardiomyocytes, Endothelium, Epithelial_cells, Mesoderm, Muscle_cells, Neural_crest_PNS_neurons, White_blood_cells) and will result in NA predictions.”


Warning message in assign_cells(sub_scores, group_assignment = ct_pred$predicted):
“Some group assignments (Neural_crest_PNS_glia, Primitive_erythroid, Definitive_erythroid, Megakaryocytes, unassigned) do not match groups in the score matrix (Cardiomyocytes, Endothelium, Epithelial_cells, Mesoderm, Muscle_cells, Neural_crest_PNS_neurons, White_blood_cells) and will result in NA predictions.”


In [86]:
# get all samples cell type predictions into 1 stage-specific file
newdf = c()
for(id in 4:6){
    df1 = read.delim(paste0(stages[id], '_', samples[id], '_Qiu_E10.5_celltypes.csv'), sep = ',')
    newdf = rbind(newdf, df1)
}
dim(newdf)

[1] 25515     4

In [87]:
# save
write.table(newdf, file = 'stage17_Qiu_celltypes.csv',
            sep = ',', row.names = F, col.names = T, quote = F)